# Fine-Tuning BERT as a `RewardModel`

1. First, intall `transformers`, `tlr`, and `codecarbon`.

In [1]:
!pip install transformers trl codecarbon -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.5/7.5 MB 52.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.0/118.0 kB 16.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.8/179.8 kB 24.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 29.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 113.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 79.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 251.2/251.2 kB 28.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.3/519.3 kB 45.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.4/66.4 kB 8.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.1/53.1 kB 7.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 15.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 24.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

2. Downloas the `reward-aira-dataset-comparisons` from the Hub.

In [2]:
import os
from datasets import load_dataset

project = "RewardModelPT"

os.makedirs(project, exist_ok=True)

dataset = load_dataset("nicholasKluge/reward-aira-dataset", split="portuguese")

print("Dataset loaded.")

display(dataset.to_pandas())

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating english split:   0%|          | 0/32675 [00:00<?, ? examples/s]

Generating portuguese split:   0%|          | 0/32675 [00:00<?, ? examples/s]

Dataset loaded.


instruction  \
0      Estarei em Roma no próximo mês e gostaria de s...   
1              Como determino o valor de um item antigo.   
2      A engenharia de recursos sempre melhora o dese...   
3         Qual é a diferença entre um oval e um círculo.   
4                    Qual é a história do Canal de Suez.   
...                                                  ...   
32670  É verdade que o núcleo da Terra é feito de ferro?   
32671  Estou fazendo um experimento científico, mas n...   
32672            Quanto exercício preciso fazer por dia.   
32673  Quais são os erros mais comuns no planejamento...   
32674  Estou planejando um acampamento para este fim ...   

                                         chosen_response  \
0      Que bom saber que você visitará Roma! Roma est...   
1      Determinar o valor de um item antigo pode ser ...   
2      A engenharia de recursos é uma etapa crítica n...   
3      Um oval é uma forma esticada que é mais longa ...   
4      O Canal de Suez é uma via navegável artificial...   
...                                                  ...   
32670  Sim, é geralmente aceito que o núcleo da Terra...   
32671  Claro! Ficarei feliz em ajudá-lo a solucionar ...   
32672  A quantidade de exercício que você precisa faz...   
32673  Existem vários erros comuns que as pessoas pod...   
32674  Claro! Ficarei feliz em ajudá-lo a encontrar a...   

                                       rejected_response  
0      Roma é uma cidade repleta de atrações e pontos...  
1      Para determinar o valor de um item antigo, pes...  
2      Para otimizar o desempenho do aprendizado de m...  
3      A principal diferença entre um oval e um círcu...  
4      O Canal de Suez é uma via navegável artificial...  
...                                                  ...  
32670  Sim, é verdade que o núcleo da Terra é feito d...  
32671  Sim, certamente posso ajudá-lo a solucionar o ...  
32672  Depende do seu estilo de vida e objetivos de c...  
32673  Não fazer orçamento para despesas inesperadas....  
32674  Sugiro pesquisar acampamentos próximos à sua l...  

[32675 rows x 3 columns]

3. Download your base model for fine-tuning. Here he are using `bert-base-cased` for the English reward model and `bert-base-portuguese-cased` for the Portuguse version.

In [3]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch

model_name = "neuralmind/bert-base-portuguese-cased"

model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1)
tokenizer = AutoTokenizer.from_pretrained(model_name)

if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token
    model.config.pad_token_id = model.config.eos_token_id

print(f"Model ({model_name}) ready.")

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at neuralmind/bert-base-portuguese-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Model (neuralmind/bert-base-portuguese-cased) ready.


4. Preprocess the dataset to be compatible with the `RewardTrainer` from `tlr`.

In [4]:
def preprocess(examples):
    kwargs = {"padding": "max_length", "truncation": True, "max_length": 400, "return_tensors": "pt"}

    prompt_plus_chosen_response = examples["instruction"] + "[SEP]" + examples["chosen_response"]
    prompt_plus_rejected_response = examples["instruction"] + "[SEP]" + examples["rejected_response"]

    tokens_chosen = tokenizer.encode_plus(prompt_plus_chosen_response, **kwargs)
    tokens_rejected = tokenizer.encode_plus(prompt_plus_rejected_response, **kwargs)

    return {
        "input_ids_chosen": tokens_chosen["input_ids"][0], "attention_mask_chosen": tokens_chosen["attention_mask"][0],
        "input_ids_rejected": tokens_rejected["input_ids"][0], "attention_mask_rejected": tokens_rejected["attention_mask"][0]
    }

formatted_dataset = dataset.map(preprocess)

Map:   0%|          | 0/32675 [00:00<?, ? examples/s]

5. Train your model while tracking the CO2 emissions. 🌱

In [6]:
from transformers import TrainingArguments
from codecarbon import EmissionsTracker
from trl import RewardTrainer

tracker = EmissionsTracker(
    project_name=f"{project}_emissions",
    log_level="critical",
    output_dir=f"/content/{project}",
    output_file=f"{project}_emissions.csv",
)

training_args = TrainingArguments(
    output_dir=f"/content/{project}",
    per_device_train_batch_size=42,
    do_eval=False,
    evaluation_strategy="no",
    save_strategy="steps",
    logging_strategy="steps",
    logging_steps=200,
    max_steps = 1_200,
    save_steps = 400,
    learning_rate = 5e-5,
)

trainer = RewardTrainer(
    model=model,
    args=training_args,
    tokenizer=tokenizer,
    train_dataset=formatted_dataset,
)

tracker.start()
trainer.train()
tracker.stop()

/usr/local/lib/python3.10/dist-packages/trl/trainer/reward_trainer.py:124: UserWarning: When using RewardDataCollatorWithPadding, you should set `max_length` in the RewardTrainer's init it will be set to `512` by default, but you should do it yourself in the future.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/reward_trainer.py:138: UserWarning: When using RewardDataCollatorWithPadding, you should set `remove_unused_columns=False` in your TrainingArguments we have set it for you, but you should do it yourself in the future.
  warnings.warn(
[codecarbon INFO @ 21:23:31] [setup] RAM Tracking...
[codecarbon INFO @ 21:23:31] [setup] GPU Tracking...
[codecarbon INFO @ 21:23:31] Tracking Nvidia GPU via pynvml
[codecarbon INFO @ 21:23:31] [setup] CPU Tracking...
[codecarbon WARNING @ 21:23:31] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon WARNING @ 21:23:33] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please 

[codecarbon INFO @ 21:23:48] Energy consumed for RAM : 0.000130 kWh. RAM Power : 31.305280208587646 W
[codecarbon INFO @ 21:23:48] Energy consumed for all GPUs : 0.000882 kWh. Total GPU Power : 211.55806198193085 W
[codecarbon INFO @ 21:23:48] Energy consumed for all CPUs : 0.000177 kWh. Total CPU Power : 42.5 W
[codecarbon INFO @ 21:23:48] 0.001189 kWh of electricity used since the beginning.
[codecarbon INFO @ 21:23:48] Energy consumed for RAM : 0.000130 kWh. RAM Power : 31.305280208587646 W
[codecarbon INFO @ 21:23:48] Energy consumed for all GPUs : 0.000896 kWh. Total GPU Power : 214.9890583922895 W
[codecarbon INFO @ 21:23:48] Energy consumed for all CPUs : 0.000177 kWh. Total CPU Power : 42.5 W
[codecarbon INFO @ 21:23:48] 0.001204 kWh of electricity used since the beginning.
[codecarbon INFO @ 21:24:03] Energy consumed for RAM : 0.000261 kWh. RAM Power : 31.305280208587646 W
[codecarbon INFO @ 21:24:03] Energy consumed for all GPUs : 0.002009 kWh. Total GPU Power : 270.584933468

0.0797799671652134

6. Test your RewardModel!

In [1]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

tokenizer = AutoTokenizer.from_pretrained("nicholasKluge/RewardModelPT-2")
rewardModel = AutoModelForSequenceClassification.from_pretrained("nicholasKluge/RewardModelPT-2")

rewardModel.eval()
rewardModel.to(device)

# Define the question and response
prompt = "Por que a ética da IA é importante?"

response_good = "A ética da IA é importante por vários motivos convincentes:\n\n1.**Impacto social**: As tecnologias de IA estão se tornando cada vez mais integradas a vários aspectos da sociedade, afetando tudo, desde saúde e educação até finanças e aplicação da lei. Considerações éticas garantem que os sistemas de IA contribuam positivamente para a sociedade e minimizem os possíveis danos.\n\n2. **Vieses e justiça**: Os sistemas de IA podem herdar vieses presentes nos dados em que são treinados, levando a resultados injustos ou discriminatórios. Considerações éticas pressionam pelo desenvolvimento de algoritmos imparciais que tratem todos os indivíduos de forma justa, independentemente de seu histórico.\n\n3. **Transparência e responsabilidade**: Muitos sistemas de IA operam como caixas pretas, dificultando a compreensão de como chegam às suas decisões. As diretrizes éticas enfatizam a importância da transparência, permitindo que os usuários compreendam a lógica por trás dos resultados gerados pela IA e responsabilizando os desenvolvedores por quaisquer consequências negativas.\n\nEm resumo, a ética da IA é vital para garantir que a inteligência artificial beneficie a sociedade, respeitando os direitos humanos fundamentais, a justiça, a transparência, a responsabilidade e o bem-estar da humanidade em longo prazo. Ela ajuda a enfrentar os desafios impostos pelo rápido avanço das tecnologias de IA e orienta seu desenvolvimento de forma a se alinhar com nossos valores compartilhados."
response_bad = "Quem se importa com a ética da IA? É apenas um monte de reclamações sobre o fato de os humanos criarem e usarem IA e reclamarem do que as máquinas fazem."

# Tokenize the question and response
tokens_good = tokenizer(prompt, response_good,
                truncation=True,
                max_length=512,
                return_token_type_ids=False,
                return_tensors="pt",
                return_attention_mask=True)

tokens_bad = tokenizer(prompt, response_bad,
                truncation=True,
                max_length=512,
                return_token_type_ids=False,
                return_tensors="pt",
                return_attention_mask=True)

tokens_good.to(device)
tokens_bad.to(device)

score_good = rewardModel(**tokens_good)[0].item()
score_bad = rewardModel(**tokens_bad)[0].item()

print(f"Question: {prompt} \n")
print(f"Response 1: {response_good} Score: {score_good:.3f}")
print(f"Response 2: {response_bad} Score: {score_bad:.3f}")


Question: Por que a ética da IA é importante? 

Response 1: A ética da IA é importante por vários motivos convincentes:

1.**Impacto social**: As tecnologias de IA estão se tornando cada vez mais integradas a vários aspectos da sociedade, afetando tudo, desde saúde e educação até finanças e aplicação da lei. Considerações éticas garantem que os sistemas de IA contribuam positivamente para a sociedade e minimizem os possíveis danos.

2. **Vieses e justiça**: Os sistemas de IA podem herdar vieses presentes nos dados em que são treinados, levando a resultados injustos ou discriminatórios. Considerações éticas pressionam pelo desenvolvimento de algoritmos imparciais que tratem todos os indivíduos de forma justa, independentemente de seu histórico.

3. **Transparência e responsabilidade**: Muitos sistemas de IA operam como caixas pretas, dificultando a compreensão de como chegam às suas decisões. As diretrizes éticas enfatizam a importância da transparência, permitindo que os usuários compr

Done! 🤗